In [393]:
import numpy as np
import pandas as pd
import dash
from dash.dependencies import Input, Output
import dash_core_components as dcc
import dash_html_components as html
import plotly.plotly as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

In [313]:
ksprojects=pd.read_csv("C:/Users/Anon/Python/kickstarter/ks-projects-201801.csv",encoding = 'utf8')
#ksprojects=pd.read_csv("https://perso.esiee.fr/~hamamic/cgi-bin/R/kickstarter/ks-projects-201801.csv",encoding = 'utf8')
df = ksprojects
df = df.fillna(0)

In [314]:
df.drop(['usd pledged'],axis=1,inplace=True)

df['deadline'] = pd.to_datetime(df['deadline'])
df['launched'] = pd.to_datetime(df['launched'])

df = df.query("state != 'live' & state != 'undefined' & country != 'N,0\"' ")
df = df.query('20090101000000 < launched < 20180101000000')

df = df.assign(funding_percentage = (df.usd_pledged_real/df.usd_goal_real)*100)
df = df.assign(avrg_per_bckers = df.usd_pledged_real/df.backers)
df = df.assign(days_to_complete = df.deadline-df.launched)
df = df.assign(year = df.launched.dt.year)

df.days_to_complete = df.days_to_complete.dt.days

df.replace([np.inf, -np.inf], np.nan)
df = df.fillna(0)

In [294]:
#df.groupby('year').size().tolist()
#df['year'].value_counts().tolist()
iplot([go.Scatter(y=df.groupby('year').size().tolist(),x=sorted(df.year.unique()))])

In [363]:
#df1 = df.groupby(["year","state"])["backers"].sum()

#trace1 = go.Scatter(
#    x = sorted(df.year.unique()),
#    y = [(df[(df.year == i) & (df.state=='failed')]['backers'].sum()) for i in sorted(df.year.unique())],
#    name = 'failed'
#)

iplot(
    [go.Scatter(
        x = sorted(df.year.unique()),
        y = [(df[(df.year == i) & (df.state==j)]['backers'].sum()) for i in sorted(df.year.unique())], name = j) 
     for j in df.state.unique()]
    +[go.Scatter(
        x = sorted(df.year.unique()),
        y = [(df[df.year == i]['backers'].sum()) for i in sorted(df.year.unique())],
        name = 'sum')]
)


In [365]:
#[(df[df.year == i]['days_to_complete']) for i in sorted(df.year.unique())]
#trace11 = go.Box(y = df[df.year == 2009]['days_to_complete'].tolist(),name=2009)
iplot([go.Box(y = df[df.year == i]['days_to_complete'].tolist(),name=str(i),boxpoints= False) for i in sorted(df.year.unique())])



In [398]:
df1 = df[(df.year == 2017) & (df.country == 'FR')].agg({'days_to_complete': ['size', 'std', 'min','mean', 'max', 'sum'], 
                                                  'backers': ['size', 'std', 'min','mean', 'max', 'sum'],
                                                  'usd_pledged_real': ['size', 'std', 'min','mean', 'max', 'sum'],
                                                  'usd_goal_real': ['size', 'std', 'min','mean', 'max', 'sum'],
                                                  'funding_percentage': ['size', 'std', 'min','mean', 'max', 'sum'],
                                                  'avrg_per_bckers': ['size', 'std', 'min','mean', 'max', 'sum']
                                                 })

iplot(ff.create_table(df1, index=True))

In [458]:
print(df[(df.year == 2010) & (df.country == 'US')].state.value_counts())
print(df[(df.year == 2010) & (df.country == 'US')].state.value_counts().to_dict().keys())
print(df[(df.year == 2010) & (df.country == 'US')].state.value_counts().to_dict().values())
#df[(df.year == 2009) & (df.country == 'US')].state.unique()


iplot([go.Histogram(histfunc = "count",x = list(df[(df.year == 2015) & (df.country == 'FR')].state))])


failed        4984
successful    4593
canceled       926
suspended       16
Name: state, dtype: int64
dict_keys(['failed', 'successful', 'canceled', 'suspended'])
dict_values([4984, 4593, 926, 16])


In [490]:
trace1 = go.Bar(
    x=df[(df.year == 2017) & (df.country == 'US') & (df.state == "failed")].main_category.value_counts().keys(),
    y=df[(df.year == 2017) & (df.country == 'US') & (df.state == "failed")].main_category.value_counts(),
    name='failed'
)



data = [go.Bar(
    x=df[(df.year == 2017) & (df.country == 'US') & (df.state == i)].main_category.value_counts().keys(),
    y=df[(df.year == 2017) & (df.country == 'US') & (df.state == i)].main_category.value_counts(),
    name=str(i)
) for i in df.state.unique()]

iplot(go.Figure(data=data, layout = go.Layout(barmode='stack')))

In [477]:
#df[(df.year == 2017) & (df.country == 'US') & (df.state == "failed")].main_category.value_counts().keys()
df[(df.year == 2017) & (df.country == 'US') & (df.state == "failed")].main_category.value_counts()



Technology      1958
Film & Video    1782
Publishing      1769
Music           1518
Games           1473
Food            1444
Fashion         1394
Design          1330
Art             1091
Crafts           620
Comics           403
Photography      292
Journalism       253
Theater          204
Dance             81
Name: main_category, dtype: int64